# Arkhamdb Decklists Data Loading 
Created: 2021-11-02  
Updated: 2021-11-02  
Author: Spencer Simon

## Overview

This notebook uses data downloaded from [arkhamdb.com](https://arkhamdb.com) using their [public api](https://arkhamdb.com/api/).  The data downloading and cleaning is performed in the arkhamdb-data repository. 

This data is transformed and used to create a racing bar chart of investigator popularity over time in this notebook.  

## Setup

### Install and import libraries

In [3]:
import sys
!{sys.executable} -m pip install bar_chart_race --user

  Using cached bar_chart_race-0.1.0-py3-none-any.whl (156 kB)
You should consider upgrading via the '/Library/Frameworks/Python.framework/Versions/3.7/bin/python3 -m pip install --upgrade pip' command.


In [88]:
import pandas as pd
from datetime import datetime
import bar_chart_race as bcr
import matplotlib.pyplot as plt

In [43]:
pd.set_option('display.max_columns', 50)

### Load Data

In [5]:
df = pd.read_csv('../arkhamdb-data/investigator_popularity_raw.csv')

In [6]:
df.head()

id                        name        date_creation  investigator_code  \
0   1   Roland Banks Starter Deck  2016-09-02 13:17:02               1001   
1   2    Wendy Adams Starter Deck  2016-09-02 13:18:34               1005   
2   3              I'm Half Crazy  2016-10-12 07:59:47               1002   
3   4  Roland Banks, Just a G-Man  2016-10-12 16:50:58               1001   
4   6         Orphan's First deck  2016-10-15 22:39:06               1005   

  investigator_name  create_year  create_month  create_day  
0      Roland Banks         2016             9           2  
1       Wendy Adams         2016             9           2  
2      Daisy Walker         2016            10          12  
3      Roland Banks         2016            10          12  
4       Wendy Adams         2016            10          15

In [58]:
df.shape

(30235, 9)

## Data Preparation

### Drop duplicate decks

In [53]:
df_temp = df.drop_duplicates(
    subset = ['name', 'date_creation'],
    keep = 'last').reset_index(drop = True)

In [56]:
df_temp.shape

(19878, 9)

In [60]:
print(f"Number of duplicate decks dropped: {df.shape[0] - df_temp.shape[0]}")

Number of duplicate decks dropped: 10357


### Create date only field (without time)

In [61]:
df_temp['date'] = pd.to_datetime(df_temp['date_creation']).dt.date

In [63]:
df_temp.head()

id                        name        date_creation  investigator_code  \
0   1   Roland Banks Starter Deck  2016-09-02 13:17:02               1001   
1   2    Wendy Adams Starter Deck  2016-09-02 13:18:34               1005   
2   3              I'm Half Crazy  2016-10-12 07:59:47               1002   
3   4  Roland Banks, Just a G-Man  2016-10-12 16:50:58               1001   
4   6         Orphan's First deck  2016-10-15 22:39:06               1005   

  investigator_name  create_year  create_month  create_day        date  
0      Roland Banks         2016             9           2  2016-09-02  
1       Wendy Adams         2016             9           2  2016-09-02  
2      Daisy Walker         2016            10          12  2016-10-12  
3      Roland Banks         2016            10          12  2016-10-12  
4       Wendy Adams         2016            10          15  2016-10-15

### Drop all fields except investigator name and date

In [64]:
df_small = df_temp[["date", "investigator_name"]]

In [66]:
df_small.head()

date investigator_name
0  2016-09-02      Roland Banks
1  2016-09-02       Wendy Adams
2  2016-10-12      Daisy Walker
3  2016-10-12      Roland Banks
4  2016-10-15       Wendy Adams

### Get count of decks built per investigator per day

In [67]:
counts_series = df_small.groupby(['date', 'investigator_name']).size()
df_counts = counts_series.to_frame(name = 'count').reset_index()

In [77]:
df_counts.tail()

date  investigator_name  count
14337  2021-10-31         Lola Hayes      1
14338  2021-10-31       Roland Banks      2
14339  2021-10-31        Silas Marsh      1
14340  2021-10-31  Trish Scarborough      1
14341  2021-10-31     William Yorick      1

### Pivot df to wide format

In [70]:
df_wide = pd.pivot_table(df_counts, values='count', index = 'date', 
                         columns = ['investigator_name'], aggfunc=np.sum, fill_value=0)

In [72]:
df_wide.tail(6)

investigator_name  "Ashcan" Pete  "Skids" O'Toole  Agnes Baker  Akachi Onyele  \
date                                                                            
2021-10-26                     0                0            0              0   
2021-10-27                     0                0            1              0   
2021-10-28                     0                0            0              0   
2021-10-29                     0                0            1              0   
2021-10-30                     1                0            0              0   
2021-10-31                     1                0            1              1   

investigator_name  Amanda Sharpe  Bob Jenkins  Calvin Wright  Carolyn Fern  \
date                                                                         
2021-10-26                     0            0              0             0   
2021-10-27                     0            0              3             0   
2021-10-28                     0            0              1             0   
2021-10-29                     0            1              0             0   
2021-10-30                     0            0              0             0   
2021-10-31                     0            0              0             0   

investigator_name  Daisy Walker  Daniela Reyes  Dexter Drake  Diana Stanley  \
date                                                                          
2021-10-26                    1              0             0              0   
2021-10-27                    0              0             0              0   
2021-10-28                    0              0             0              0   
2021-10-29                    0              0             0              0   
2021-10-30                    0              0             0              0   
2021-10-31                    1              0             0              0   

investigator_name  Father Mateo  Finn Edwards  Gloria Goldberg  \
date                                                             
2021-10-26                    0             0                0   
2021-10-27                    0             0                0   
2021-10-28                    0             0                0   
2021-10-29                    0             0                0   
2021-10-30                    0             0                0   
2021-10-31                    0             0                0   

investigator_name  Harvey Walters  Jacqueline Fine  Jenny Barnes  Jim Culver  \
date                                                                           
2021-10-26                      0                0             1           0   
2021-10-27                      0                0             0           0   
2021-10-28                      0                0             0           0   
2021-10-29                      0                1             0           0   
2021-10-30                      0                0             0           0   
2021-10-31                      1                0             1           0   

investigator_name  Joe Diamond  Leo Anderson  Lily Chen  Lola Hayes  \
date                                                                  
2021-10-26                   0             1          0           0   
2021-10-27                   0             0          1           0   
2021-10-28                   0             0          0           0   
2021-10-29                   2             0          0           2   
2021-10-30                   0             0          0           0   
2021-10-31                   0             0          0           1   

investigator_name  Luke Robinson  Mandy Thompson  Marie Lambeau  \
date                                                              
2021-10-26                     0               1              0   
2021-10-27                     0               0              0   
2021-10-28                     0               0              0   
2021-10-29         

### Add in rows for missing dates

In [82]:
# New index range is min to max date
new_index = pd.date_range(df_wide.index.min(), df_wide.index.max()) 
df_wide = df_wide.reindex(new_index, fill_value=0)

In [83]:
df_wide

investigator_name  "Ashcan" Pete  "Skids" O'Toole  Agnes Baker  Akachi Onyele  \
2016-09-02                     0                0            0              0   
2016-09-03                     0                0            0              0   
2016-09-04                     0                0            0              0   
2016-09-05                     0                0            0              0   
2016-09-06                     0                0            0              0   
...                          ...              ...          ...            ...   
2021-10-27                     0                0            1              0   
2021-10-28                     0                0            0              0   
2021-10-29                     0                0            1              0   
2021-10-30                     1                0            0              0   
2021-10-31                     1                0            1              1   

investigator_name  Amanda Sharpe  Bob Jenkins  Calvin Wright  Carolyn Fern  \
2016-09-02                     0            0              0             0   
2016-09-03                     0            0              0             0   
2016-09-04                     0            0              0             0   
2016-09-05                     0            0              0             0   
2016-09-06                     0            0              0             0   
...                          ...          ...            ...           ...   
2021-10-27                     0            0              3             0   
2021-10-28                     0            0              1             0   
2021-10-29                     0            1              0             0   
2021-10-30                     0            0              0             0   
2021-10-31                     0            0              0             0   

investigator_name  Daisy Walker  Daniela Reyes  Dexter Drake  Diana Stanley  \
2016-09-02                    0              0             0              0   
2016-09-03                    0              0             0              0   
2016-09-04                    0              0             0              0   
2016-09-05                    0              0             0              0   
2016-09-06                    0              0             0              0   
...                         ...            ...           ...            ...   
2021-10-27                    0              0             0              0   
2021-10-28                    0              0             0              0   
2021-10-29                    0              0             0              0   
2021-10-30                    0              0             0              0   
2021-10-31                    1              0             0              0   

investigator_name  Father Mateo  Finn Edwards  Gloria Goldberg  \
2016-09-02                    0             0                0   
2016-09-03                    0             0                0   
2016-09-04                    0             0                0   
2016-09-05                    0             0                0   
2016-09-06                    0             0                0   
...                         ...           ...              ...   
2021-10-27                    0             0                0   
2021-10-28                    0             0                0   
2021-10-29                    0             0                0   
2021-10-30                    0             0                0   
2021-10-31                    0             0                0   

investigator_name  Harvey Walters  Jacqueline Fine  Jenny Barnes  Jim Culver  \
2016-09-02                      0                0             0           0   
2016-09-03                      0                0             0           0   
2016-09-04                      0                0             0           0   
2016-09-05                  

### Calculate rolling sum to get the number of decks built that month 
Use 30 days as an approximation for the month

In [95]:
df_wide_sums = df_wide.copy()
cols=list(df_wide.columns)

df_wide_sums["30d sum " + pd.Index(cols)] = df_wide[cols].rolling(window=30).sum()

In [99]:
df_wide_sums.head(31)

investigator_name  "Ashcan" Pete  "Skids" O'Toole  Agnes Baker  Akachi Onyele  \
2016-09-02                     0                0            0              0   
2016-09-03                     0                0            0              0   
2016-09-04                     0                0            0              0   
2016-09-05                     0                0            0              0   
2016-09-06                     0                0            0              0   
2016-09-07                     0                0            0              0   
2016-09-08                     0                0            0              0   
2016-09-09                     0                0            0              0   
2016-09-10                     0                0            0              0   
2016-09-11                     0                0            0              0   
2016-09-12                     0                0            0              0   
2016-09-13                     0                0            0              0   
2016-09-14                     0                0            0              0   
2016-09-15                     0                0            0              0   
2016-09-16                     0                0            0              0   
2016-09-17                     0                0            0              0   
2016-09-18                     0                0            0              0   
2016-09-19                     0                0            0              0   
2016-09-20                     0                0            0              0   
2016-09-21                     0                0            0              0   
2016-09-22                     0                0            0              0   
2016-09-23                     0                0            0              0   
2016-09-24                     0                0            0              0   
2016-09-25                     0                0            0              0   
2016-09-26                     0                0            0              0   
2016-09-27                     0                0            0              0   
2016-09-28                     0                0            0              0   
2016-09-29                     0                0            0              0   
2016-09-30                     0                0            0              0   
2016-10-01                     0                0            0              0   
2016-10-02                     0                0            0              0   

investigator_name  Amanda Sharpe  Bob Jenkins  Calvin Wright  Carolyn Fern  \
2016-09-02                     0            0              0             0   
2016-09-03                     0            0              0             0   
2016-09-04                     0            0              0             0   
2016-09-05                     0            0              0             0   
2016-09-06                     0            0              0             0   
2016-09-07                     0            0              0             0   
2016-09-08                     0            0              0             0   
2016-09-09                     0            0              0             0   
2016-09-10                     0            0              0             0   
2016-09-11                     0            0              0             0   
2016-09-12                     0            0              0             0   
2016-09-13                     0            0              0             0   
2016-09-14                     0            0              0             0   
2016-09-15                     0            0              0             0   
2016-09-16                     0            0              0             0   
2016-09-17                     0            0              0             0   
2016-09-18                     0            0              0             0   
201

In [ ]:
# Make a basic time series plot of the data

## Create Racing Bar Chart

Updates:
- Make df with only the rolling sums
- Make col names of this new df just investigator names
- decide on if 30 day sums are best measure
- Make bcr with options: images, top X bars, colors, etc.

In [100]:
bcr_html = bcr.bar_chart_race(df=df_wide_sums.tail(20), 
                              #img_label_folder=,
                              filename=None)

/Users/spencersimon/Library/Python/3.7/lib/python/site-packages/matplotlib/backends/backend_agg.py:238: RuntimeWarning: Glyph 127 missing from current font.
  font.set_text(s, 0.0, flags=flags)
/Users/spencersimon/Library/Python/3.7/lib/python/site-packages/matplotlib/backends/backend_agg.py:238: RuntimeWarning: Glyph 128 missing from current font.
  font.set_text(s, 0.0, flags=flags)
/Users/spencersimon/Library/Python/3.7/lib/python/site-packages/matplotlib/backends/backend_agg.py:238: RuntimeWarning: Glyph 129 missing from current font.
  font.set_text(s, 0.0, flags=flags)
/Users/spencersimon/Library/Python/3.7/lib/python/site-packages/matplotlib/backends/backend_agg.py:238: RuntimeWarning: Glyph 130 missing from current font.
  font.set_text(s, 0.0, flags=flags)
/Users/spencersimon/Library/Python/3.7/lib/python/site-packages/matplotlib/backends/backend_agg.py:238: RuntimeWarning: Glyph 131 missing from current font.
  font.set_text(s, 0.0, flags=flags)
/Users/spencersimon/Library/Py

/Users/spencersimon/Library/Python/3.7/lib/python/site-packages/bar_chart_race/_make_chart.py:286: UserWarning: FixedFormatter should only be used together with FixedLocator
  ax.set_yticklabels(self.df_values.columns)
/Users/spencersimon/Library/Python/3.7/lib/python/site-packages/bar_chart_race/_make_chart.py:287: UserWarning: FixedFormatter should only be used together with FixedLocator
  ax.set_xticklabels([max_val] * len(ax.get_xticks()))


In [101]:
bcr_html

In [ ]:
bcr.bar_chart_race(
    df=df_wide,
    filename='covid19_horiz.mp4',
    orientation='h',
    sort='desc',
    n_bars=6,
    fixed_order=False,
    fixed_max=True,
    steps_per_period=10,
    interpolate_period=False,
    label_bars=True,
    bar_size=.95,
    period_label={'x': .99, 'y': .25, 'ha': 'right', 'va': 'center'},
    period_fmt='%B %d, %Y',
    period_summary_func=lambda v, r: {'x': .99, 'y': .18,
                                      's': f'Total deaths: {v.nlargest(6).sum():,.0f}',
                                      'ha': 'right', 'size': 8, 'family': 'Courier New'},
    perpendicular_bar_func='median',
    period_length=500,
    figsize=(5, 3),
    dpi=144,
    cmap='dark12',
    title='COVID-19 Deaths by Country',
    title_size='',
    bar_label_size=7,
    tick_label_size=7,
    shared_fontdict={'family' : 'Helvetica', 'color' : '.1'},
    scale='linear',
    writer=None,
    fig=None,
    bar_kwargs={'alpha': .7},
    filter_column_colors=False)